In [9]:
import osmnx as ox
import geopandas as gpd
from shapely.geometry import MultiPoint, MultiPolygon
import folium
from folium import plugins
import os


In [10]:
# set path 
current_path = os.getcwd()
root_path = os.path.dirname(current_path)
raw_path = os.path.join(root_path, 'data', 'raw')
process_path = os.path.join(root_path, 'data', 'processed')
# print(raw_path)

In [5]:

# Specify the name of the city and country
place_name = "Atlanta, USA"

# Download the point of interest data
pois = ox.features_from_place(place_name, tags={'amenity':'parking'})

# see how many features were returned
print(len(pois), 'points of interest')


1365 points of interest


In [29]:

# plot out the pois
# ax = ox.plot_footprints(pois)

# plot with folium

# plot the geodataframe with folium
m = folium.Map(location=[33.7868794367165, -84.3855107579268], zoom_start=11, tiles='cartodb positron')
# add poi's 'name' column as pop-up labels for the markers
folium.features.GeoJson(pois, 
						fill_color="red", fill_opacity=0.5, stroke=False,
						tooltip=folium.GeoJsonTooltip(fields=['parking','access','fee','capacity']),
						).add_to(m)

polygon_path = os.path.join(raw_path, 'City_of_Atlanta_Neighborhood_Statistical_Areas/City_of_Atlanta_Neighborhood_Statistical_Areas.shp')
polygon = gpd.read_file(polygon_path)
polygon.head()
# add polygon layer to m
folium.GeoJson(data=polygon, fill=False).add_to(m)

m

In [15]:
pois.head(10)

amenity                    geometry       name  \
element_type osmid                                                        
node         496141022   parking  POINT (-84.39143 33.76207)        NaN   
             496141023   parking  POINT (-84.39142 33.76115)        NaN   
             497397032   parking  POINT (-84.32157 33.75499)        NaN   
             534431138   parking  POINT (-84.38312 33.75679)        NaN   
             567065914   parking  POINT (-84.35175 33.79235)        NaN   
             600429864   parking  POINT (-84.39090 33.76088)  Interpark   
             681262448   parking  POINT (-84.39408 33.75466)        NaN   
             795904771   parking  POINT (-84.39821 33.79183)        NaN   
             1127136673  parking  POINT (-84.38043 33.75540)        NaN   
             1179861872  parking  POINT (-84.38051 33.75715)        NaN   

                        old_name operator layer      parking access  fee  \
element_type osmid                                                         
node         496141022       NaN      NaN    -1  underground    NaN  NaN   
             496141023       NaN      NaN    -1  underground    NaN  NaN   
             497397032       NaN      NaN   NaN      surface    yes   no   
             534431138       NaN      NaN   NaN          NaN    NaN  NaN   
             567065914       NaN      NaN   NaN          NaN    NaN  NaN   
             600429864       NaN      NaN   NaN          NaN    NaN  NaN   
             681262448       NaN      NaN   NaN      surface    NaN  NaN   
             795904771       NaN      NaN   NaN          NaN    NaN  NaN   
             1127136673      NaN      NaN   NaN      surface    yes  yes   
             1179861872      NaN      NaN   NaN          NaN    NaN  NaN   

                        capacity  ... phone smoothness access:conditional  \
element_type osmid                ...                                       
node         496141022       NaN  ...   NaN        NaN                NaN   
             496141023       NaN  ...   NaN        NaN                NaN   
             497397032       NaN  ...   NaN        NaN                NaN   
             534431138       100  ...   NaN        NaN                NaN   
             567065914       NaN  ...   NaN        NaN                NaN   
             600429864       NaN  ...   NaN        NaN                NaN   
             681262448       NaN  ...   NaN        NaN                NaN   
             795904771       NaN  ...   NaN        NaN                NaN   
             1127136673       20  ...   NaN        NaN                NaN   
             1179861872       20  ...   NaN        NaN                NaN   

                        maxstay:conditional building:part email image ways  \
element_type osmid                                                           
node         496141022                  NaN           NaN   NaN   NaN  NaN   
             496141023                  NaN           NaN   NaN   NaN  NaN   
             497397032                  NaN           NaN   NaN   NaN  NaN   
             534431138                  NaN           NaN   NaN   NaN  NaN   
             567065914                  NaN           NaN   NaN   NaN  NaN   
             600429864                  NaN           NaN   NaN   NaN  NaN   
             681262448                  NaN           NaN   NaN   NaN  NaN   
             795904771                  NaN           NaN   NaN   NaN  NaN   
             1127136673                 NaN           NaN   NaN   NaN  NaN   
             1179861872                 NaN           NaN   NaN   NaN  NaN   

                        type roof:shape  
element_type osmid                       
node         496141022   NaN        NaN  
             496141023   NaN        NaN  
             497397032   NaN        NaN  
             534431138   NaN        NaN  
             567065914   NaN        NaN  
             600429864   NaN        NaN  
             

In [ ]:
# Remove rows with empty geometries
pois = pois[pois.geometry.notnull()]

# Remove rows with invalid geometries
pois = pois[pois.geometry.is_valid]
pois.geometry = pois.geometry.apply(lambda x: x[0] if isinstance(x, MultiPoint) else x)
# pois.geometry = pois.geometry.apply(lambda x: x[0] if isinstance(x, MultiPolygon) else x)
# if the field is a list, drop the list and keep the first element
pois.geometry = pois.geometry.apply(lambda x: x[0] if isinstance(x, list) else x)
# save the data as a geojson file
pois.to_file('../data/raw/parking.geojson', driver='GeoJSON')




In [20]:
pois.head()
# convert to geodataframe
pois = gpd.GeoDataFrame(pois)
pois.head()
# check the type of pois
type(pois)

pois.columns
# check the type of each column and return a dictionary
pois.dtypes.to_dict()
# turn pois.dtypes into a dataframe

# check which field is list class



# save to geojson
# pois.to_file('../data/raw/parking.shp')

{'amenity': dtype('O'),
 'geometry': <geopandas.array.GeometryDtype at 0x133699d10>,
 'name': dtype('O'),
 'old_name': dtype('O'),
 'operator': dtype('O'),
 'layer': dtype('O'),
 'parking': dtype('O'),
 'access': dtype('O'),
 'fee': dtype('O'),
 'capacity': dtype('O'),
 'covered': dtype('O'),
 'area': dtype('O'),
 'gatech:LASTUPDATE': dtype('O'),
 'gatech:SUBTYPE': dtype('O'),
 'location': dtype('O'),
 'source': dtype('O'),
 'gatech:ATL_BLDG_': dtype('O'),
 'gatech:ATL_BLDG_I': dtype('O'),
 'gatech:PERIMETER': dtype('O'),
 'gatech:Reference_': dtype('O'),
 'ownership': dtype('O'),
 'wheelchair': dtype('O'),
 'note': dtype('O'),
 'brand': dtype('O'),
 'brand:wikidata': dtype('O'),
 'brand:wikipedia': dtype('O'),
 'operator:wikidata': dtype('O'),
 'operator:wikipedia': dtype('O'),
 'level': dtype('O'),
 'addr:state': dtype('O'),
 'website': dtype('O'),
 'addr:street': dtype('O'),
 'comment': dtype('O'),
 'fixme': dtype('O'),
 'review_requested': dtype('O'),
 'nodes': dtype('O'),
 'buildi

In [ ]:
# Remove rows with empty geometries
pois = pois[pois.geometry.notnull()]

# Remove rows with invalid geometries
pois = pois[pois.geometry.is_valid]
pois.geometry = pois.geometry.apply(lambda x: x[0] if isinstance(x, MultiPoint) else x)
pois.to_file('../data/raw/parking.shp')
# Convert MultiPolygons to Polygons
# pois.geometry = pois.geometry.apply(lambda x: x[0] if isinstance(x, MultiPolygon) else x)

In [38]:
# read data in the data/final
gdf_final = gpd.read_file('../data/final/5finalists.geojson')

# add parkingn poi and gdf_final to m_final
m_final = folium.Map(location=[33.7868794367165, -84.3855107579268], zoom_start=11, tiles='cartodb positron')
# add gdf_final to m_final
folium.features.GeoJson(gdf_final, 
						fill_color="blue", fill_opacity=0.3, stroke=True,
						tooltip=folium.GeoJsonTooltip(fields=['NEIGHBORHO']),
						).add_to(m_final)
# add polygon layer to m
# folium.GeoJson(data=polygon, fill=False).add_to(m_final)
# add poi's 'name' column as pop-up labels for the markers
folium.features.GeoJson(pois, 
						fill_color="red", fill_opacity=0.8, stroke=False,
						tooltip=folium.GeoJsonTooltip(fields=['parking','access','fee','capacity']),
						).add_to(m_final)
m_final